<a href="https://colab.research.google.com/github/atstuyuki/mediapipe/blob/main/mediapipe_shoulder_toCSV_20221213.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# セットアップ

さまざまなカメラアングルから肩の外転角度を算出　訓練用のCSVを作成する

In [ ]:
#google driveのマウント
'''from google.colab import drive
drive.mount('/content/drive')'''

"from google.colab import drive\ndrive.mount('/content/drive')"

#誤検出が多かったので、min_detection_confidence　0.8に変更

In [1]:
# ライブラリーのインストール
!pip install numpy==1.19.3
!pip install mediapipe
# 初期設定 holistic とPoseを用意する　検出感度は0.5＞＞変更可能
import mediapipe as mp
import cv2
mp_holistic = mp.solutions.holistic
mp_pose = mp.solutions.pose
# Initialize MediaPipe Holistic.
holistic = mp_holistic.Holistic(
    static_image_mode=True, min_detection_confidence=0.7)
pose= mp_pose.Pose(
    static_image_mode=True, min_detection_confidence=0.7)
# Prepare DrawingSpec for drawing the face landmarks later.
mp_drawing = mp.solutions.drawing_utils 
drawing_spec = mp_drawing.DrawingSpec(color=[225,0,200],thickness=2, circle_radius=1) #color=[B,G,R]で指定,線の太さと〇の色も指定可能

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 14.9 MB 5.1 MB/s 
  Attempting uninstall: numpy
    Found existing installation: numpy 1.21.6
    Uninstalling numpy-1.21.6:
      Successfully uninstalled numpy-1.21.6
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.9.2 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.
jaxlib 0.3.25+cuda11.cudnn805 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.
jax 0.3.25 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.
cmdstanpy 1.0.8 requires numpy>=1.21, but you have numpy 1.19.3 which is incompatible.


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 33.0 MB 90.2 MB/s 
  Attempting uninstall: flatbuffers
    Found existing installation: flatbuffers 1.12
    Uninstalling flatbuffers-1.12:
      Successfully uninstalled flatbuffers-1.12
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.9.2 requires flatbuffers<2,>=1.12, but you have flatbuffers 22.12.6 which is incompatible.
tensorflow 2.9.2 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.


正解の肩外転角度を入力 スライダーバーで10度刻みに指定

In [2]:
true_angle = 120 #@param {type:"slider", min:0, max:180, step:10}


カメラの設置角度指定

In [3]:
cam_angle= 30  #@param {type:"slider", min:-60, max:60, step:15}

右手か左手を指定(is_right Yes=1, NO=0)

In [4]:
is_right_hand=1  #@param ["0", "1"] {allow-input: true}

保存ファイル名を指定

In [5]:
movie_name= "kusu2"#@param {type:"string"}

In [6]:
#手元の動画をgoogle colabにupload

from google.colab import files
import os
uploaded = files.upload()
#uploadedは辞書型なのでファイル名を取り出し、絶対パスを取得してfullpathという変数を当てる
for k in uploaded.keys():
  print('file name:',k)
fullpath=os.path.abspath(k)
print('fullpath:',fullpath)

Saving Movie_01_(Movie_01_(I30 free))720_Trim.mp4 to Movie_01_(Movie_01_(I30 free))720_Trim.mp4
file name: Movie_01_(Movie_01_(I30 free))720_Trim.mp4
fullpath: /content/Movie_01_(Movie_01_(I30 free))720_Trim.mp4


In [7]:
cap = cv2.VideoCapture(fullpath) #動画の読み込み
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH)) #幅
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT)) #高
frame_rate = int(cap.get(cv2.CAP_PROP_FPS)) #FPS
fourcc = cv2.VideoWriter_fourcc('m','p','4','v') #mp4出力
out = cv2.VideoWriter('out.mp4', fourcc, frame_rate, (width, height))
print('width:',width)
print('height:',height)
print('frame rate:',frame_rate)

#3次元座標の角度計算の定義
def calculate_3D_angle(a,b,c):
    a = np.array(a) # First
    b = np.array(b) # Mid
    c = np.array(c) # End
    #0がx座標　１がｙ座標　２がｚ座標
    #ベクトルを定義 長さと内積からコサインを計算
    vec_a=a-b
    vec_c=c-b
    len_vec_a=np.linalg.norm(vec_a)
    len_vec_c=np.linalg.norm(vec_c)
    inner_product=np.inner(vec_a, vec_c)
    cos=inner_product/(len_vec_a*len_vec_c)
    
    #角度（ラジアン）の計算
    rad=np.arccos(cos)
    
    #ラジアンから度数へ変換
    angle=np.rad2deg(rad)
        
    return angle

#2次元からの角度計算の定義
def calculate_2D_angle(a,b,c):
  a=np.array(a)#firtst
  b=np.array(b)#second
  c=np.array(c)#third
  #[x,y,z]座標から[x,y]のみスライスしてベクトルを作成
  vec_a=a[0:2]-b[0:2]
  vec_c=c[0:2]-b[0:2]
  len_vec_a=np.linalg.norm(vec_a)
  len_vec_c=np.linalg.norm(vec_c)
  inner_product=np.inner(vec_a, vec_c)
  cos=inner_product/(len_vec_a*len_vec_c)
    
#角度（ラジアン）の計算
  rad=np.arccos(cos)
#ラジアンから度数へ変換
  angle=np.rad2deg(rad)
        
  return angle


width: 720
height: 1280
frame rate: 30


各種測定関数の定義

In [8]:
#体軸からの肩の外転角度測定
#3次元座標の角度計算の定義
def calculate_3D_shoulder_angle(a,b,c,d,e):
    a = np.array(a) # 右肘
    b = np.array(b) # 右肩
    c = np.array(c) # 左肩
    #c1=[b[0], c[1],b[2]]#右肩のx, 左肩のy、右肩のzを取得
    d = np.array(d) # 右股
    e = np.array(e) # 左股
    #0がx座標　１がｙ座標　２がｚ座標
    #中点を定義
    global shoulder_mid
    shoulder_mid = (b+c)/2 #肩の中心座標
    global hip_mid
    hip_mid = (d+e)/2 #股関節の中心座標　world系では0になるはず
    #ベクトルを定義 長さと内積からコサインを計算
    vec_a=hip_mid-shoulder_mid #体軸のベクトル
    vec_b=a-b
    len_vec_a=np.linalg.norm(vec_a)
    len_vec_b=np.linalg.norm(vec_b)
    inner_product=np.inner(vec_a, vec_b)
    cos=inner_product/(len_vec_a*len_vec_b)
    
    #角度（ラジアン）の計算
    rad=np.arccos(cos)
    
    #ラジアンから度数へ変換
    angle=np.rad2deg(rad)
        
    return angle

#2次元からの角度計算の定義
def calculate_2D_shoulder_angle(a,b,c,d,e):
    a = np.array(a) # 右肘
    b = np.array(b) # 右肩
    c = np.array(c) # 左肩
    #c1=[b[0], c[1],b[2]]#右肩のx, 左肩のy、右肩のzを取得
    d = np.array(d) # 右股
    e = np.array(e) # 左股
    #0がx座標　１がｙ座標　２がｚ座標
    #中点を定義
    shoulder_mid = (b+c)/2 #肩の中心座標
    hip_mid = (d+e)/2 #股関節の中心座標　world系では0になるはず
  #[x,y,z]座標から[x,y]のみスライスしてベクトルを作成
    vec_a=hip_mid[0:2]-shoulder_mid[0:2]#体軸のベクトル
    vec_b=a[0:2]-b[0:2]
    len_vec_a=np.linalg.norm(vec_a)
    len_vec_b=np.linalg.norm(vec_b)
    inner_product=np.inner(vec_a, vec_b)
    cos=inner_product/(len_vec_a*len_vec_b)
    
#角度（ラジアン）の計算
    rad=np.arccos(cos)
#ラジアンから度数へ変換
    angle=np.rad2deg(rad)
        
    return angle

#面積　sizeの計算 2Dの3点から外積を算出　
def calc_size(a, b, c):
    a=np.array(a[0:2])#先端の座標1(x,yのみ)
    b=np.array(b[0:2])#先端の座標2
    c=np.array(c[0:2])#基部の座標

    vec1=a-c
    vec2=b-c
    
    size=np.cross(vec1,vec2)*10#数字が小さいので10倍しておく
    size=np.abs(size)#絶対値をとる
    return size


#pointの距離計測の関数 a-b（2点間の座標）間の距離を基準となる距離(c-dの距離）で除したものとする
def point_distance(a,b,c,d):
    a=np.array(a)#遠位関節の座標
    b=np.array(b)#近位関節の座標
    c=np.array(c)#基準関節の座標1
    d=np.array(d)#基準関節の座標2
    
    dist1=np.linalg.norm(a-b)
    dist2=np.linalg.norm(c-d)
    distance=dist1/dist2
    return distance 

# サンプルビデオの読み込み＋静止画に分解

In [9]:
# video2images
import os
import shutil
import cv2

# 既にimagesフォルダーがあれば削除
if os.path.isdir('images'):
    shutil.rmtree('images')

os.makedirs('images', exist_ok=True)
 
def video_2_images(video_file= fullpath,   
                   image_dir='./images/', 
                   image_file='%s.png'):
 
    # Initial setting
    i = 0
    interval = 1#適宜調整
    length = 3500
    
    cap = cv2.VideoCapture(video_file)
    while(cap.isOpened()):
        flag, frame = cap.read()  
        if flag == False:  
                break
        if i == length*interval:
                break
        if i % interval == 0:    
           cv2.imwrite(image_dir+image_file % str(int(i/interval)).zfill(6), frame)
        i += 1 
    cap.release()  
 
def main():
    video_2_images()
    
if __name__ == '__main__':
    main()

In [10]:
#pose_landmarkのリストを取得して配列に変換

import numpy as np
landmarklist=[]#空の配列を作成
for index in range(len(mp_holistic.PoseLandmark)):
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_x')
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_y')
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_z')
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_visibility')
#リストをarrayに変換
landmarklist=np.array(landmarklist).reshape(1,-1)
#landmarkshape の内容の確認
print('landmark list data type:',landmarklist.dtype)
print('landmark list:',landmarklist)
print('landmark list shape:',landmarklist.shape)


landmark list data type: <U27
landmark list: [['NOSE_x' 'NOSE_y' 'NOSE_z' 'NOSE_visibility' 'LEFT_EYE_INNER_x'
  'LEFT_EYE_INNER_y' 'LEFT_EYE_INNER_z' 'LEFT_EYE_INNER_visibility'
  'LEFT_EYE_x' 'LEFT_EYE_y' 'LEFT_EYE_z' 'LEFT_EYE_visibility'
  'LEFT_EYE_OUTER_x' 'LEFT_EYE_OUTER_y' 'LEFT_EYE_OUTER_z'
  'LEFT_EYE_OUTER_visibility' 'RIGHT_EYE_INNER_x' 'RIGHT_EYE_INNER_y'
  'RIGHT_EYE_INNER_z' 'RIGHT_EYE_INNER_visibility' 'RIGHT_EYE_x'
  'RIGHT_EYE_y' 'RIGHT_EYE_z' 'RIGHT_EYE_visibility' 'RIGHT_EYE_OUTER_x'
  'RIGHT_EYE_OUTER_y' 'RIGHT_EYE_OUTER_z' 'RIGHT_EYE_OUTER_visibility'
  'LEFT_EAR_x' 'LEFT_EAR_y' 'LEFT_EAR_z' 'LEFT_EAR_visibility'
  'RIGHT_EAR_x' 'RIGHT_EAR_y' 'RIGHT_EAR_z' 'RIGHT_EAR_visibility'
  'MOUTH_LEFT_x' 'MOUTH_LEFT_y' 'MOUTH_LEFT_z' 'MOUTH_LEFT_visibility'
  'MOUTH_RIGHT_x' 'MOUTH_RIGHT_y' 'MOUTH_RIGHT_z'
  'MOUTH_RIGHT_visibility' 'LEFT_SHOULDER_x' 'LEFT_SHOULDER_y'
  'LEFT_SHOULDER_z' 'LEFT_SHOULDER_visibility' 'RIGHT_SHOULDER_x'
  'RIGHT_SHOULDER_y' 'RIGHT_SHOULDER_z' 

# MediaPipeで静止画を処理

In [11]:
import cv2
from google.colab.patches import cv2_imshow
import numpy as np
import glob
import time
#変数の初期化
rtshoulderAnglelist=[]
rtshoulderAbductionlist=[]
rtshoulder_3DAnglelist=[]
rtshoulder_3DAbductionlist=[]

ltshoulderAnglelist=[]
ltshoulderAbductionlist=[]
ltshoulder_3DAnglelist=[]
ltshoulder_3DAbductionlist=[]

true_angle_list=[]
cam_angle_list=[]
is_right_hand_list=[]
timelist=[]

#各関節の3次元座標もリスト化する

"""
nose_x_list=[]
nose_y_list=[]
nose_z_list=[]
rtelbow_x_list=[]
rtelbow_y_list=[]
rtelbow_z_list=[]
rtshoulder_x_list=[]
rtshoulder_y_list=[]
rtshoulder_z_list=[]

ltelbow_x_list=[]
ltelbow_y_list=[]
ltelbow_z_list=[]
ltshoulder_x_list=[]
ltshoulder_y_list=[]
ltshoulder_z_list=[]

rthip_x_list=[]
rthip_y_list=[]
rthip_z_list=[]
lthip_x_list=[]
lthip_y_list=[]
lthip_z_list=[]
"""
#肘股関節距離/体軸長
rtelbowhip_distlist=[]
ltelbowhip_distlist=[]
#上腕の長さを体幹の長さで割ったものを変数とする
rtarm_distlist=[]
ltarm_distlist=[]
#股関節幅と体幹軸の長さの比
rthip_distlist=[]
lthip_distlist=[]
#肩幅と体幹軸の長さの比
rtshoulder_distlist=[]
ltshoulder_distlist=[]

data_land = np.zeros((0,132))

# image file names to files in list format
files=[]
for name in sorted(glob.glob('./images/*.png')):
    files.append(name)

# Read images with OpenCV.
images = {name: cv2.imread(name) for name in files}
w = width             # 画像の横幅を取得
h = height            # 画像の縦幅を取得

for name, image in images.items():
  # Convert the BGR image to RGB and process it with MediaPipe Pose.
  if image is None:
      break
  results = pose.process(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
  landmarks = results.pose_landmarks
  if landmarks is None:
      print('検出できなかったフレーム番号:',name)
      continue
   #各検出ポイントをarrayに変換
   #world座標系にすると左手の精度がでないので変更した
  rtshoulder=[results.pose_world_landmarks.landmark[12].x,results.pose_world_landmarks.landmark[12].y,results.pose_world_landmarks.landmark[12].z]
  rtelbow=[results.pose_world_landmarks.landmark[14].x,results.pose_world_landmarks.landmark[14].y,results.pose_world_landmarks.landmark[14].z]
  #rtwrist=[results.pose_world_landmarks.landmark[16].x,results.pose_world_landmarks.landmark[16].y,results.pose_world_landmarks.landmark[16].z]
  rthip=[results.pose_world_landmarks.landmark[24].x,results.pose_world_landmarks.landmark[24].y,results.pose_world_landmarks.landmark[24].z]
  ltshoulder=[results.pose_world_landmarks.landmark[11].x,results.pose_world_landmarks.landmark[11].y,results.pose_world_landmarks.landmark[11].z]
  ltelbow=[results.pose_world_landmarks.landmark[13].x,results.pose_world_landmarks.landmark[13].y,results.pose_world_landmarks.landmark[13].z]
  lthip=[results.pose_world_landmarks.landmark[23].x,results.pose_world_landmarks.landmark[23].y,results.pose_world_landmarks.landmark[23].z]
  nose=[results.pose_world_landmarks.landmark[0].x,results.pose_world_landmarks.landmark[0].y,results.pose_world_landmarks.landmark[0].z]
  #midshoulder=(np.array(rtshoulder)+np.array(ltshoulder))/2
  #midhip=(np.array(rthip)+np.array(lthip))/2
  #3D座標から角度を計算 2Dか3Dか選ぶ
  #rtelbowAngleは右肩-右肘-右手関節
  #rtelbowAngle=180-calculate_2D_angle(rtshoulder,rtelbow,rtwrist)
  #rtelbow_3DAngle=180-calculate_3D_angle(rtshoulder,rtelbow,rtwrist)
  #rtshoulderAngleは左肩-右肩-右肘
  rtshoulderAngle=calculate_2D_angle(ltshoulder,rtshoulder,rtelbow)
  rtshoulder_3DAngle=calculate_3D_angle(ltshoulder,rtshoulder,rtelbow)

  ltshoulderAngle=calculate_2D_angle(rtshoulder,ltshoulder,ltelbow)
  ltshoulder_3DAngle=calculate_3D_angle(rtshoulder,ltshoulder,ltelbow)  
  #rtshoulderAbductionは右股-右肩-右ひじ
  rtshoulderAbduction=calculate_2D_angle(rthip,rtshoulder,rtelbow)
  rtshoulder_3DAbduction=calculate_3D_angle(rthip,rtshoulder,rtelbow)

  ltshoulderAbduction=calculate_2D_angle(lthip,ltshoulder,ltelbow)
  ltshoulder_3DAbduction=calculate_3D_angle(lthip,ltshoulder,ltelbow)
  #肘-股関節距離/体幹長
  rtelbowhip_dist=point_distance(rtelbow,rthip,rtshoulder,rthip)
  ltelbowhip_dist=point_distance(ltelbow,lthip,ltshoulder,lthip)
  #上腕長/体幹長さの距離の計算
  rtarm_dist=point_distance(rtelbow, rtshoulder, rtshoulder,rthip)
  ltarm_dist=point_distance(ltelbow,ltshoulder,ltshoulder, lthip)

  #肩幅/体幹長
  rtshoulder_dist=point_distance(rtshoulder, ltshoulder,rtshoulder,rthip)
  ltshoulder_dist=point_distance(ltshoulder,ltelbow,ltshoulder,lthip)
  #股関節幅/体幹長
  rthip_dist=point_distance(rthip,lthip,rtshoulder,rthip)
  lthip_dist=point_distance(rthip,lthip,ltshoulder,lthip)
#リストに計算した変数を追加してゆく
  rtshoulderAnglelist.append(rtshoulderAngle)
  rtshoulderAbductionlist.append(rtshoulderAbduction)
  rtshoulder_3DAnglelist.append(rtshoulder_3DAngle)
  rtshoulder_3DAbductionlist.append(rtshoulder_3DAbduction)

  ltshoulderAnglelist.append(ltshoulderAngle)
  ltshoulderAbductionlist.append(ltshoulderAbduction)
  ltshoulder_3DAnglelist.append(ltshoulder_3DAngle)
  ltshoulder_3DAbductionlist.append(ltshoulder_3DAbduction)

  true_angle_list.append(true_angle)
  cam_angle_list.append(cam_angle)
  is_right_hand_list.append(is_right_hand)
  timelist.append(time.time())
  #肘股関節距離/体軸長
  rtelbowhip_distlist.append(rtelbowhip_dist)
  ltelbowhip_distlist.append(ltelbowhip_dist)

  #上腕長/体幹長のリスト
  rtarm_distlist.append(rtarm_dist)
  ltarm_distlist.append(ltarm_dist)

  #肩幅/体幹長のリスト
  rtshoulder_distlist.append(rtshoulder_dist)
  ltshoulder_distlist.append(ltshoulder_dist)

  #股関節幅と体幹軸の長さの比
  rthip_distlist.append(rthip_dist)
  lthip_distlist.append(lthip_dist)

  # Draw pose landmarks.
  annotated_image = image.copy()
  # Get Landmarks
  #landmarks=results.pose_landmarks.landmark
 
  """
  Holisticを使用しない場合はこの部分をコメントアウト
  
  mp_drawing.draw_landmarks(annotated_image, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS)
  mp_drawing.draw_landmarks(annotated_image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS)
  mp_drawing.draw_landmarks(
      image=annotated_image, 
      landmark_list=results.face_landmarks, 
      connections=mp_holistic.FACEMESH_TESSELATION,
      landmark_drawing_spec=drawing_spec,
      connection_drawing_spec=drawing_spec)
  """
  mp_drawing.draw_landmarks(
        image=annotated_image, 
        landmark_list=results.pose_landmarks, 
        connections=mp_pose.POSE_CONNECTIONS,
        landmark_drawing_spec=drawing_spec,
        connection_drawing_spec=drawing_spec)
  
  #get coordinate poseの33か所の3次元座標データと確信度(visibilisty)をすべて結合してCSVに変換
  data_land2 = np.zeros((1,3))
    
  for x in range (0,33):#pose_landmarksかpose_world_landmarksか選ぶ
      data1 = results.pose_world_landmarks.landmark[x].x
      data2 = results.pose_world_landmarks.landmark[x].y
      data3 = results.pose_world_landmarks.landmark[x].z
      data4 = results.pose_world_landmarks.landmark[x].visibility
      keydata = np.hstack((data1,data2,data3,data4)).reshape(1,-1)
      data_land2 = np.hstack((data_land2,keydata))

  data_land2 = data_land2[:,3:]
  data_land = np.vstack((data_land,data_land2))

  final_data= np.vstack((landmarklist,data_land))
  
  cv2.imwrite(name, annotated_image)  

#savetxtではデータの型が合わないと保存でき無いことがあるのでfmtで文字の型を指定
  np.savetxt('keypoint_results.csv',final_data,delimiter = ',',fmt = '%s')


In [12]:
import pandas as pd
landmark_df = pd.read_csv('keypoint_results.csv')
display(landmark_df)

NOSE_x    NOSE_y    NOSE_z  NOSE_visibility  LEFT_EYE_INNER_x  \
0    0.018993 -0.604778 -0.314309         0.999993          0.024723   
1    0.026362 -0.598463 -0.326214         0.999995          0.031822   
2    0.027262 -0.613903 -0.310085         0.999989          0.031342   
3    0.015197 -0.610377 -0.315139         0.999988          0.020026   
4    0.026873 -0.614009 -0.314890         0.999989          0.032369   
..        ...       ...       ...              ...               ...   
334  0.078685 -0.648821 -0.218212         0.999846          0.079224   
335  0.079889 -0.642361 -0.224905         0.999811          0.081304   
336  0.084729 -0.638628 -0.219016         0.999793          0.085801   
337  0.077528 -0.614852 -0.275052         0.999859          0.079924   
338  0.082723 -0.639939 -0.233525         0.999832          0.082965   

     LEFT_EYE_INNER_y  LEFT_EYE_INNER_z  LEFT_EYE_INNER_visibility  \
0           -0.645941         -0.301733                   0.999977   
1           -0.639842         -0.313708                   0.999985   
2           -0.655127         -0.298483                   0.999960   
3           -0.651959         -0.304532                   0.999956   
4           -0.655058         -0.302442                   0.999961   
..                ...               ...                        ...   
334         -0.681245         -0.201210                   0.999757   
335         -0.675030         -0.208696                   0.999694   
336         -0.671154         -0.203010                   0.999657   
337         -0.647720         -0.260578                   0.999769   
338         -0.672861         -0.217714                   0.999719   

     LEFT_EYE_x  LEFT_EYE_y  ...  RIGHT_HEEL_z  RIGHT_HEEL_visibility  \
0      0.025023   -0.646163  ...      0.135553               0.770463   
1      0.032117   -0.640048  ...      0.150916               0.771281   
2      0.031642   -0.655348  ...      0.174344               0.842975   
3      0.020348   -0.652188  ...      0.183977               0.826218   
4      0.032663   -0.655255  ...      0.176972               0.815738   
..          ...         ...  ...           ...                    ...   
334    0.079748   -0.682050  ...      0.094067               0.812867   
335    0.081826   -0.675842  ...      0.104861               0.799430   
336    0.086322   -0.671962  ...      0.096342               0.775045   
337    0.080488   -0.648573  ...      0.078123               0.769884   
338    0.083495   -0.673671  ...      0.100220               0.806630   

     LEFT_FOOT_INDEX_x  LEFT_FOOT_INDEX_y  LEFT_FOOT_INDEX_z  \
0             0.109893           0.850100           0.095409   
1             0.102197           0.855202           0.105605   
2             0.115681           0.853154           0.140555   
3             0.111263           0.853167           0.138769   
4             0.101586           0.850056           0.137112   
..                 ...                ...                ...   
334           0.096792           0.834222           0.119217   
335           0.095815           0.833029           0.119647   
336           0.098567           0.830686           0.115141   
337           0.113733           0.847072           0.072056   
338           0.099307           0.829328           0.119905   

     LEFT_FOOT_INDEX_visibility  RIGHT_FOOT_INDEX_x  RIGHT_FOOT_INDEX_y  \
0                      0.958947            0.021990            0.889630   
1                      0.962548            0.010126            0.889035   
2                      0.972418            0.017954            0.892637   
3                      0.971189            0.003338            0.884551   
4                      0.969162            0.011810            0.886497   
..                          ...                 ...                 ...   
334                    0.907604           -0.029192            0.857340   
335                    0.909425           -0.038029    

In [13]:
#zip関数でリストをまとめてデータフレーム化
import pandas as pd
zipped=zip(true_angle_list,cam_angle_list,is_right_hand_list,
rtshoulderAnglelist,rtshoulderAbductionlist,rtshoulder_3DAnglelist,
rtshoulder_3DAbductionlist,ltshoulderAnglelist,ltshoulderAbductionlist,
ltshoulder_3DAnglelist,ltshoulder_3DAbductionlist,
rtelbowhip_distlist,ltelbowhip_distlist,
rtarm_distlist,ltarm_distlist,
rtshoulder_distlist,ltshoulder_distlist,rthip_distlist,lthip_distlist)
df = pd.DataFrame(zipped, columns = ['true_angle','cam_angle','is_right_hand',
'rtshoulderAngle','rtshoulderAbduction','rtshoulder_3DAngle',
'rtshoulder_3DAbduction','ltshoulderAngle','ltshoulderAbduction',
'ltshoulder_3DAngle','ltshoulder_3DAbduction',
'rtelbowhip_distratio','ltelbowhip_distratio',
'rtarm_distratio','ltarm_distratio',
'rtshoulder_distratio','ltshoulder_distratio','rthip_distratio','lthip_distratio'])

In [14]:
#時間列を初期化してSeriesへ
#timelistの開始数字を0に変更
np.array(timelist[0])
#d=np.full(len(timelist),timelist[0])#すべての要素がtimelistの１番目の値でlen(timelist)の行列を作成
#timelistの時間を初期化（1番目の要素を0として行列の引き算
deltatime=np.array(timelist)-np.full(len(timelist),timelist[0])
deltatime = pd.Series(deltatime)
deltatime.name='deltatime'
#deltatimeとデータフレーム(df)の結合
df= pd.concat([deltatime, df],axis=1)
#最終データの概要を確認
display(df)

deltatime  true_angle  cam_angle  is_right_hand  rtshoulderAngle  \
0     0.000000         120         30              1       110.908566   
1     0.138371         120         30              1       111.208456   
2     0.261525         120         30              1       114.551595   
3     0.387020         120         30              1       115.803280   
4     0.519973         120         30              1       115.134278   
..         ...         ...        ...            ...              ...   
334  55.578111         120         30              1       140.823938   
335  55.780566         120         30              1       140.497721   
336  55.991751         120         30              1       141.256861   
337  56.192925         120         30              1       140.886681   
338  56.400353         120         30              1       141.929140   

     rtshoulderAbduction  rtshoulder_3DAngle  rtshoulder_3DAbduction  \
0              28.036202          108.125215               27.397919   
1              28.236573          108.529796               27.524351   
2              30.171197          111.908142               29.523252   
3              32.304191          113.609238               31.556067   
4              31.745790          112.850093               31.106664   
..                   ...                 ...                     ...   
334           151.622967          145.921933              146.963283   
335           151.774577          145.257953              147.687285   
336           151.303960          145.892701              147.844591   
337           151.317737          144.693921              149.372329   
338           150.345970          146.870060              147.311337   

     ltshoulderAngle  ltshoulderAbduction  ltshoulder_3DAngle  \
0          93.707455            10.358586           95.313839   
1          93.383240             9.621557           94.835962   
2          91.778945             9.974333           93.131712   
3          93.050125            10.312095           93.980755   
4          91.996955             9.062255           93.113268   
..               ...                  ...                 ...   
334       117.956487            14.574368          117.099260   
335       118.562127            15.552570          117.631090   
336       119.415853            15.999512          118.777653   
337       119.238683            16.140971          118.349891   
338       118.645420            15.344394          118.408254   

     ltshoulder_3DAbduction  rtelbowhip_distratio  ltelbowhip_distratio  \
0                 10.925685              0.594209              0.547015   
1                 10.871981              0.592078              0.545680   
2                 11.451633              0.617236              0.552688   
3                 12.378345              0.637469              0.558594   
4                 11.231323              0.628382              0.555165   
..                      ...                   ...                   ...   
334               14.909700              1.377020              0.563165   
335               16.181111              1.373309              0.562964   
336               16.259882              1.375719              0.557089   
337               19.505270              1.382122              0.566194   
338               15.605131              1.376213              0.563734   

     rtarm_distratio  ltarm_distratio  rtshoulder_distratio  \
0           0.511893         0.468744              0.669226   
1           0.516684         0.470005              0.661761   
2           0.498469         0.464297              0.666102   
3           0.488137         0.460930              0.662603   
4           0.498500         0.460971              0.663361   
..               ...              ...                   ...   
334         0.426181         0.465380              0.519046   
335         0.419865         0.471235              0.519982   
336         0.

In [15]:
#2つのデータフレームを結合
df_final=pd.concat([df, landmark_df], axis=1)
#最終データの概要を確認
display(df_final)

deltatime  true_angle  cam_angle  is_right_hand  rtshoulderAngle  \
0     0.000000         120         30              1       110.908566   
1     0.138371         120         30              1       111.208456   
2     0.261525         120         30              1       114.551595   
3     0.387020         120         30              1       115.803280   
4     0.519973         120         30              1       115.134278   
..         ...         ...        ...            ...              ...   
334  55.578111         120         30              1       140.823938   
335  55.780566         120         30              1       140.497721   
336  55.991751         120         30              1       141.256861   
337  56.192925         120         30              1       140.886681   
338  56.400353         120         30              1       141.929140   

     rtshoulderAbduction  rtshoulder_3DAngle  rtshoulder_3DAbduction  \
0              28.036202          108.125215               27.397919   
1              28.236573          108.529796               27.524351   
2              30.171197          111.908142               29.523252   
3              32.304191          113.609238               31.556067   
4              31.745790          112.850093               31.106664   
..                   ...                 ...                     ...   
334           151.622967          145.921933              146.963283   
335           151.774577          145.257953              147.687285   
336           151.303960          145.892701              147.844591   
337           151.317737          144.693921              149.372329   
338           150.345970          146.870060              147.311337   

     ltshoulderAngle  ltshoulderAbduction  ...  RIGHT_HEEL_z  \
0          93.707455            10.358586  ...      0.135553   
1          93.383240             9.621557  ...      0.150916   
2          91.778945             9.974333  ...      0.174344   
3          93.050125            10.312095  ...      0.183977   
4          91.996955             9.062255  ...      0.176972   
..               ...                  ...  ...           ...   
334       117.956487            14.574368  ...      0.094067   
335       118.562127            15.552570  ...      0.104861   
336       119.415853            15.999512  ...      0.096342   
337       119.238683            16.140971  ...      0.078123   
338       118.645420            15.344394  ...      0.100220   

     RIGHT_HEEL_visibility  LEFT_FOOT_INDEX_x  LEFT_FOOT_INDEX_y  \
0                 0.770463           0.109893           0.850100   
1                 0.771281           0.102197           0.855202   
2                 0.842975           0.115681           0.853154   
3                 0.826218           0.111263           0.853167   
4                 0.815738           0.101586           0.850056   
..                     ...                ...                ...   
334               0.812867           0.096792           0.834222   
335               0.799430           0.095815           0.833029   
336               0.775045           0.098567           0.830686   
337               0.769884           0.113733           0.847072   
338               0.806630           0.099307           0.829328   

     LEFT_FOOT_INDEX_z  LEFT_FOOT_INDEX_visibility  RIGHT_FOOT_INDEX_x  \
0             0.095409                    0.958947            0.021990   
1             0.105605                    0.962548            0.010126   
2             0.140555                    0.972418            0.017954   
3             0.138769                    0.971189            0.003338   
4             0.137112                    0.969162            0.011810   
..                 ...                         ...                 ...   
334           0.119217                    0.907604           -0.029192   
335           0.119647                    0.909425           -0.038029   
336        

In [16]:
#CSVに保存
df_final.to_csv(movie_name+'.csv',index=False)

# 処理した画像をmp4動画に変換


In [17]:
# 既に output.mp4 があれば削除
import os
if os.path.exists('./output.mp4'):
   os.remove('./output.mp4')

! ffmpeg -r 10 -i images/%6d.png\
               -vcodec libx264 -pix_fmt yuv420p output.mp4

ffmpeg version 3.4.11-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-li

In [18]:
# --- mp4動画の再生 ---
from IPython.display import HTML
from base64 import b64encode

mp4 = open('./output.mp4', 'rb').read()
data_url = 'data:video/mp4;base64,' + b64encode(mp4).decode()
HTML(f"""
<video width="85%" height="85%" controls>
      <source src="{data_url}" type="video/mp4">
</video>""")

＊作成したmp4動画は、左側のファイル欄にある　./mediapipe/output.mp4 を右クリックするとダウンロードできます。